In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from collections import defaultdict
import itertools
import json
import logging
import math
import random
import os

from matplotlib import pyplot as plt
import pandas as pd
from PIL import ImageColor
import papermage
from papermage.magelib import Box, Entity
from papermage.recipes import CoreRecipe
from papermage.visualizers import plot_entities_on_page
from papermage.utils.annotate import group_by
from tqdm.auto import tqdm

from papermage_components.materials_recipe import MaterialsRecipe

In [3]:
logging.basicConfig(level=logging.INFO)

In [4]:
recipe = MaterialsRecipe()

INFO:MaterialsRecipe:Instantiating recipe...


GROBID server is up and running


INFO:iopath.common.file_io:URL https://www.dropbox.com/s/ukbw5s673633hsw/publaynet-tf_efficientdet_d0.pth.tar?dl=1 cached in /Users/sireeshgururaja/.torch/iopath_cache/s/ukbw5s673633hsw/publaynet-tf_efficientdet_d0.pth.tar?dl=1
INFO:timm.models._helpers:Loaded state_dict from checkpoint '/Users/sireeshgururaja/.torch/iopath_cache/s/ukbw5s673633hsw/publaynet-tf_efficientdet_d0.pth.tar?dl=1'
INFO:MaterialsRecipe:Finished instantiating recipe


In [7]:
sample_doc = recipe.from_pdf(
    # f"data/AM_Creep_Papers/On the creep performance of the Ti‐6Al‐4V alloy processed by additive manufacturing.pdf"
    # "data/AM_Creep_Papers/A creep-resistant additively manufactured Al-Ce-Ni-Mn alloy.pdf"
    "data/AM_Creep_Papers/Creep deformation and failure properties of 316 L stainless steel manufactured by laser powder bed fusion under multiaxial loading conditions.pdf"
)

INFO:MaterialsRecipe:Parsing document...
INFO:MaterialsRecipe:Rasterizing document...


No annotated file found, skipping...


INFO:MaterialsRecipe:Predicting words...
INFO:MaterialsRecipe:Predicting sentences...
INFO:MaterialsRecipe:Predicting blocks...
100%|██████████| 11/11 [00:10<00:00,  1.03it/s]
INFO:MaterialsRecipe:Predicting vila...


In [8]:
colors_list = list(ImageColor.colormap.keys())
random.seed(23)
random.shuffle(colors_list)

def highlight_relevant_entities(document):
    document_sections = {entity.metadata["section_name"] for entity in document.reading_order_sections}
    color_map = {section: color for section, color in zip(document_sections, colors_list)}

    page_images = []
    for i, page in enumerate(document.pages):
        highlighted = page.images[0]
        entities_by_section = defaultdict(list)
        for entity in page.reading_order_sections:
            entities_by_section[entity.metadata["section_name"]].append(entity)

        for section_name, section_entities in entities_by_section.items():
            highlighted = plot_entities_on_page(
                highlighted, section_entities, box_width=4, box_alpha=0.4, box_color=color_map[section_name], page_number=i
            )

        page_images.append(highlighted)
    return page_images

def plot_boxes(document, boxes):
    page = document.pages[boxes[0].page]
    filtered_boxes = [box for box in boxes if box.page == 0]
    page_image = page.images[0]
    highlighted = plot_entities_on_page(page_image, [Entity(boxes=filtered_boxes)], box_width=2, box_alpha=0.1, box_color="red")
    return highlighted


In [9]:
highlighted_doc = highlight_relevant_entities(sample_doc)

n_cols = 3
n_rows = math.ceil(len(highlighted_doc) / 3)
multiplier = 10
fig, axes = plt.subplots(nrows=n_rows, ncols=n_cols, figsize=(8.5 * multiplier, 11 * multiplier), tight_layout=True)

for ax in itertools.chain(*axes):
    ax.set_axis_off()

for i, (ax, image) in enumerate(zip(itertools.chain(*axes), highlighted_doc)):
    ax.imshow(image.to_array())
    image.save(f"data/box_highlights_p{i}.png", is_overwrite=True)